In [1]:
import numpy as np
import gurobipy as grb
import csv
import time
import statsmodels.api as sm
from joblib import Parallel,delayed

def five_variate(n,SNR,rho):
    beta1 = np.array([1,1,1,0,1])
    beta2 = np.array([-1,-1,-1,0,-1])
    p = len(beta1)
    Sigma = np.zeros((p,p));
    for i in range(p):
        for j in range(p):
            Sigma[i,j] = rho**(abs(i-j))
    X = np.random.multivariate_normal(mean =np.zeros(p), cov = Sigma, size = n)
    noise1 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta1)/SNR), size = int(n/2)) 
    noise2 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta2)/SNR), size = int(n/2)) 
    Y1 = X[:int(n/2)]@beta1 + noise1
    Y2 = X[int(n/2):]@beta2 + noise2
    Y = np.r_[Y1,Y2]
    lam = 0.1*n
    ols = sm.OLS(Y, X)
    ols_result = ols.fit()
    bigM = 10*float(1.96*(sum(ols_result.bse)))#1000

    M = grb.Model()
    M.Params.TimeLimit = 400
    beta = M.addMVar((int(n),5), lb = -grb.GRB.INFINITY)
    z = M.addMVar(len(Y) - 1, vtype = grb.GRB.BINARY)
    sum_of_sq = sum((Y[t] - sum(X[t,j]*beta[t,j] for j in range(5)))* (Y[t] - sum(X[t,j]*beta[t,j] for j in range(5))) for t in range(len(Y)))
    for t in range(len(Y)-1):
        for j in range(5):
            M.addConstr(beta[t+1,j] - beta[t,j] <= bigM*z[t])
            M.addConstr(beta[t+1,j] - beta[t,j] >= -bigM*z[t])
    #optional constratins to add more cuts
    M.addConstr(sum(z) <= 5)
    for t in range(1, len(Y) - 2):
        M.addConstr(z[t-1] + z[t] + z[t+1] <= 1)
    # l2-reg
    phi = 0.0005*n
    l2_penalty =  phi*sum(sum(beta[t,j]*beta[t,j] for j in range(5)) for t in range(len(Y)))
    M.setObjective(sum_of_sq+ lam*sum(z) + l2_penalty)
    M.optimize()
    beta_hat = [beta[t].x for t in range(len(Y))]
    z_hat = [z[t].x for t in range(len(Y)-1)]
    opt_gap = M.MIPGap
    return z_hat, opt_gap,beta_hat

SNR_list = np.array([6, 3.52, 2.07, 1.22, 0.71])
rho_list = np.array([0, 0.3, 0.7])
n_list = np.array([1000])

header = ['Repitition','Time','rho', 'SNR', 'n', 'Optimality Gap', 'Change Points']#, 'beta_hat', 'nonzero count']
f = open('simulation_five_variate_l2_reg.csv', 'w')
writer = csv.writer(f)
writer.writerow(header)
f.close()

def to_repeat(rep):
    for n in n_list:
        for SNR in SNR_list:
            for rho in rho_list:
                tik = time.time()
                z_hat, opt_gap, beta_hat = five_variate(n,SNR,rho)
                tok = time.time()
                duration = tok - tik
                cps = [idx for idx,item in enumerate(z_hat) if item == 1 ]
                # Write result
                resultrow = [rep,duration,rho,SNR, n, opt_gap, cps]
                f = open('simulation_five_variate_l2_reg.csv', 'a')
                writer = csv.writer(f)
                writer.writerow(resultrow)
                f.close()
                
Parallel(n_jobs = 8)(delayed(to_repeat)(rep) for rep in range(50)) #Tomo's machine has 8 cores.

import numpy as np
import gurobipy as grb
import csv
import time
import statsmodels.api as sm
from joblib import Parallel,delayed

def five_variate(n,SNR,rho):
    beta1 = np.array([1,1,1,0,1])
    beta2 = np.array([-1,-1,-1,0,-1])
    p = len(beta1)
    Sigma = np.zeros((p,p));
    for i in range(p):
        for j in range(p):
            Sigma[i,j] = rho**(abs(i-j))
    X = np.random.multivariate_normal(mean =np.zeros(p), cov = Sigma, size = n)
    noise1 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta1)/SNR), size = int(n/2)) 
    noise2 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta2)/SNR), size = int(n/2)) 
    Y1 = X[:int(n/2)]@beta1 + noise1
    Y2 = X[int(n/2):]@beta2 + noise2
    Y = np.r_[Y1,Y2]
    lam = 0.1*n
    ols = sm.OLS(Y, X)
    ols_result = ols.fit()
    bigM = 10*float(1.96*(sum(ols_result.bse)))#1000

    M = grb.Model()
    M.Params.TimeLimit = 400
    beta = M.addMVar((int(n),5), lb = -grb.GRB.INFINITY)
    z = M.addMVar(len(Y) - 1, vtype = grb.GRB.BINARY)
    sum_of_sq = sum((Y[t] - sum(X[t,j]*beta[t,j] for j in range(5)))* (Y[t] - sum(X[t,j]*beta[t,j] for j in range(5))) for t in range(len(Y)))
    for t in range(len(Y)-1):
        for j in range(5):
            M.addConstr(beta[t+1,j] - beta[t,j] <= bigM*z[t])
            M.addConstr(beta[t+1,j] - beta[t,j] >= -bigM*z[t])
    #optional constratins to add more cuts
    M.addConstr(sum(z) <= 5)
    for t in range(1, len(Y) - 2):
        M.addConstr(z[t-1] + z[t] + z[t+1] <= 1)
    # l1-reg
    # reference: https://support.gurobi.com/hc/en-us/community/posts/360077266711-C-sum-absolute-value-in-objective
    phi = 0.001*n
    beta_abs = M.addMVar((int(n),5)) 
    M.addConstrs(beta_abs[t, j] == grb.abs_(beta[t,j]) for j in range(5) for t in range(len(Y)))# compute absolute value for each beta
    l1_penalty =  phi*sum(sum(beta_abs[t, j] for j in range(5)) for t in range(len(Y))) # compute l1 penalty term
    M.setObjective(sum_of_sq+ lam*sum(z) + l1_penalty)
    M.optimize()
    beta_hat = [beta[t].x for t in range(len(Y))]
    z_hat = [z[t].x for t in range(len(Y)-1)]
    opt_gap = M.MIPGap
    return z_hat, opt_gap,beta_hat

SNR_list = np.array([6, 3.52, 2.07, 1.22, 0.71])
rho_list = np.array([0, 0.3, 0.7])
n_list = np.array([1000])

header = ['Repitition','Time','rho', 'SNR', 'n', 'Optimality Gap', 'Change Points']#, 'beta_hat', 'nonzero count']
f = open('simulation_five_variate_l1_reg.csv', 'w')
writer = csv.writer(f)
writer.writerow(header)
f.close()

def to_repeat(rep):
    for n in n_list:
        for SNR in SNR_list:
            for rho in rho_list:
                tik = time.time()
                z_hat, opt_gap, beta_hat = five_variate(n,SNR,rho)
                tok = time.time()
                duration = tok - tik
                cps = [idx for idx,item in enumerate(z_hat) if item == 1 ]
                # Write result
                resultrow = [rep,duration,rho,SNR, n, opt_gap, cps]
                f = open('simulation_five_variate_l1_reg.csv', 'a')
                writer = csv.writer(f)
                writer.writerow(resultrow)
                f.close()
                
Parallel(n_jobs = 8)(delayed(to_repeat)(rep) for rep in range(50)) #Tomo's machine has 8 cores.

Set parameter Username
Set parameter Username
Set parameter Username
Set parameter Username
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter


Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    8688    2.9876556e+03   0.000000e+00   2.461145e+03      5s

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    8817    3.0942079e+03   0.000000e+00   2.412545e+03      5s

Root simplex log...

Iteration    Objective       Primal Inf.    Dual Inf.      Time
    8568    2.9157469e+03   0.000000e+00   2.279297e+03      5s
   13937    2.4896137e+03   0.000000e+00   1.579645e+03     10s
   13043    2.8961260e+03   0.000000e+00   1.903584e+03     10s
   13168    2.7713842e+03   0.000000e+00   1.715942e+03     10s
   13452    2.8278156e+03   0.000000e+00   1.804273e+03     10s
   13235    2.7383047e+03   0.000000e+00   1.785373e+03     10s
   13840    2.5388111e+03   0.000000e+00   1.526181e+03     10s
   12999    2.6698308e+03   0.000000e+00   1.747408e+03     10s
   12780    2.5264289e+03   0.000000e+00   1.580218e+03     10s
   16788    2.4929418e+03   0.000000e+

    15    20 2006.34732    5  241 5224.53661 1990.33057  61.9%  52.9   50s
    23    28 1974.74722    7  236 4727.98676 1973.39400  58.3%  41.0   50s
    11    16 1944.95149    4  241 4993.78871 1944.95149  61.1%  40.5   51s
    19    24 1831.37369    6  223 4278.25612 1831.37369  57.2%  43.9   50s
    11    16 1841.31459    4  220 4470.49347 1841.31459  58.8%  43.1   50s
    15    20 1894.62684    5  228 4666.92349 1893.00131  59.4%  58.3   51s
    23    28 1948.06055    7  245 4993.78871 1948.06055  61.0%  43.0   55s
    27    32 1801.28490    8  209 4430.15887 1799.56392  59.4%  29.4   70s
H   28    32                    1996.2677780 1799.56392  9.85%  28.3   70s
    27    32 1833.03677    8  224 4278.25612 1832.44338  57.2%  40.9   70s
H   28    32                    2007.3280973 1832.44338  8.71%  39.4   70s
    27    32 2008.60078    8  243 5224.53661 1990.33057  61.9%  42.4   72s
H   28    32                    2213.8447456 1990.33057  10.1%  40.9   72s
    27    32 1941.23920  

   232   213 2093.81921   53  246 2213.84475 1990.33057  10.1%  48.7  130s
   158   130 1822.29289   34  217 1996.26778 1799.56392  9.85%  68.0  131s
   169   177 2012.78251   38  247 2174.61073 1973.39400  9.25%  47.0  131s
   126   112 1950.21527   29  246 2138.63464 1926.75385  9.91%  74.6  132s
   187   220 1968.09014   44  254 4592.15525 1950.65488  57.5%  24.7  132s
   198   201 2034.87214   48  230 2103.00890 1893.00131  10.0%  57.1  132s
   233   102 1857.76063   37  216 2007.32810 1832.44338  8.71%  82.9  132s
   204   197 1908.10974   41  222 2108.60095 1861.15535  11.7%  45.1  132s
   219   253 1981.29307   54  252 4592.15525 1950.65488  57.5%  24.9  135s
   225   238 2041.03148   53  226 2103.00890 1893.00131  10.0%  52.8  135s
   190   173 1824.31379   39  221 1996.26778 1799.56392  9.85%  61.5  137s
   276   258 2104.68273   66  238 2213.84475 1990.33057  10.1%  44.7  137s
   148   135 1951.40098   33  248 2138.63464 1926.75385  9.91%  67.7  137s
   239   212 1971.57022  

  1086   744 2155.83548   33  235 2174.61073 1973.39400  9.25%  22.5  217s
   771   836 2115.16603  194  241 4592.15525 1950.65488  57.5%  22.6  220s
  1724  1485 2132.30056  380  176 2213.84475 2008.82015  9.26%  20.2  221s
  1048   872 2074.20947  272  210 2138.63464 1926.75385  9.91%  25.2  222s
  1684  1355 2024.37636  182  236 2103.00890 1896.54328  9.82%  23.2  224s
  1847  1555 2136.28690  407  169 2213.84475 2008.82015  9.26%  19.8  225s
  1908  1520 1992.89937  263  204 2108.60095 1864.28984  11.6%  19.9  224s
  1125   940 2075.57489  292  202 2138.63464 1926.75385  9.91%  24.6  225s
   898   974 2139.37319  224  230 4592.15525 1950.65488  57.5%  22.3  229s
  2033  1629 1995.42869  295  198 2108.60095 1864.28984  11.6%  19.8  228s
  1819  1464 2028.59337  215  231 2103.00890 1896.54328  9.82%  22.5  228s
   973  1057 2142.80712  244  231 4592.15525 1950.65488  57.5%  21.7  233s
  2169  1742 1998.09563  325  190 2108.60095 1864.28984  11.6%  19.7  232s
  2104  1778 2145.35406  

...

    67    74 6874.58637   18  290 8853.19763 6826.61312  22.9%   160   90s
    79    87 6878.72861   20  292 8853.19763 6826.61312  22.9%   151   95s
    89    98 6517.71066   22  299 9027.09331 6462.00097  28.4%   110   97s
    92   100 6890.17293   24  289 8853.19763 6826.61312  22.9%   142  101s
   105   114 6531.23898   26  293 9027.09331 6462.00097  28.4%   105  102s
   107   117 6898.49393   28  282 8853.19763 6826.61312  22.9%   133  106s
   131   154 6905.91798   32  284 8853.19763 6826.61312  22.9%   123  110s
   125   142 6538.62790   30  297 9027.09331 6462.00097  28.4%   100  125s
   188   226 6551.72567   37  307 9027.09331 6462.00097  28.4%  86.3  130s
   274   297 6620.76145   58  309 9027.09331 6462.00097  28.4%  81.3  136s
   328   371 6644.48392   69  317 9027.09331 6462.00097  28.4%  79.1  141s
   402   437 6660.70052   83  315 9027.09331 6462.00097  28.4%  74.8  146s
   476   517 6688.77454  100  317 9027.09331 6462.00097  28.4%  73.2  151s
   549   589 6740.82416  

Gurobi Optimizer version 10.0.1 build v10.0.1rc0 (mac64[x86])

CPU model: Intel(R) Core(TM) i5-8257U CPU @ 1.40GHz
Thread count: 4 physical cores, 8 logical processors, using up to 8 threads

Optimize a model with 10988 rows, 10999 columns and 33960 nonzeros
Model fingerprint: 0x4ba7d1d3
Model has 15000 quadratic objective terms
Model has 5000 general constraints
Variable types: 10000 continuous, 999 integer (999 binary)
Coefficient statistics:
  Matrix range     [1e+00, 1e+01]
  Objective range  [6e-05, 1e+02]
  QObjective range [2e-10, 4e+01]
  Bounds range     [1e+00, 1e+00]
  RHS range        [1e+00, 5e+00]
         Consider reformulating model or setting NumericFocus parameter
         to avoid numerical issues.
Found heuristic solution: objective 14319.922293
Presolve added 10000 rows and 0 columns
Presolve time: 0.07s
Presolved: 20988 rows, 10999 columns, 53960 nonzeros
Presolved model has 15000 quadratic objective terms
Variable types: 10000 continuous, 999 integer (999 binary)

  1649  1740 9942.26782  394  304 12969.4969 8910.34116  31.3%  65.0  287s
  2152  2290 9815.90778  526  277 11621.7267 8752.06236  24.7%  53.7  290s
  1739  1875 9986.66141  418  307 12969.4969 8910.34116  31.3%  64.4  293s
  2289  2425 9871.76277  561  266 11621.7267 8752.06236  24.7%  52.9  296s
  1874  2048 10048.2131  445  300 12969.4969 8910.34116  31.3%  63.2  300s
  2424  2571 9912.54650  598  253 11621.7267 8752.06236  24.7%  53.1  304s
  2047  2186 10091.2437  482  291 12969.4969 8910.34116  31.3%  61.1  308s
  2570  2744 10040.4787  624  239 11621.7267 8752.06236  24.7%  53.0  313s
  2185  2331 10156.9943  510  279 12969.4969 8910.34116  31.3%  60.4  317s
  2743  2931 10099.2136  663  225 11621.7267 8752.06236  24.7%  52.6  320s
  2930  2949 10186.9369  692  216 11621.7267 8752.06236  24.7%  52.1  330s
  2330  2463 10217.5794  548  267 12969.4969 8910.34116  31.3%  59.8  335s
  2948  3125 10223.2384  705  218 11621.7267 8752.06236  24.7%  52.2  346s
  2462  2469 10328.5628  

   340   380 10451.8662   69  385 20934.6186 10017.7680  52.1%   123  192s
   379   414 10498.3181   77  381 20934.6186 10017.7680  52.1%   119  195s
H  413   438                    20913.527169 10017.7680  52.1%   117  198s
H  422   438                    20790.129677 10017.7680  51.8%   117  198s
H  430   438                    20700.681926 10017.7680  51.6%   116  198s
    71    78 11809.2183   19  353 24036.7556 11587.9755  51.8%   225  199s
   437   472 10593.9925   92  395 20700.6819 10017.7680  51.6%   116  201s
    77    86 11814.9984   20  351 24036.7556 11587.9755  51.8%   215  202s
   471   508 10627.6013  101  387 20700.6819 10017.7680  51.6%   115  206s
H  481   508                    20648.038856 10017.7680  51.5%   115  206s
    85    95 11822.0683   21  353 24036.7556 11587.9755  51.8%   202  206s
   507   553 10672.9294  111  401 20648.0389 10017.7680  51.5%   113  210s
   103   114 11858.8674   25  358 24036.7556 11587.9755  51.8%   184  212s
   552   597 10719.5238  

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]